In [16]:
import pandas as pd
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from umap import UMAP
from stopwords import gr_stopwords

pd.set_option('display.max_colwidth', 50)

In [17]:
df = pd.read_csv('data/greek_news_climate.tar.bz2')
df['published_date'] = pd.to_datetime(df['published_date'])

In [65]:
# Data cleaning 
# Removing duplicates, irrelevant articles
# and rows without summaries

df.drop_duplicates(subset = ['summary'], inplace = True)
df = df.query(" _score > 20")

mask = df['summary'].notna()
df = df[mask]

df.shape

(15913, 19)

In [66]:
news_list = df['summary'].to_list()
timestamps = df['published_date'].dt.strftime('%Y-%m-%d').to_list()

In [67]:
vectorizer_model = CountVectorizer(stop_words = gr_stopwords)

sentence_model = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2")
embeddings = sentence_model.encode(news_list, show_progress_bar=True)

topic_model = BERTopic(language = 'multilingual', nr_topics = 'auto', verbose = True, min_topic_size = 100,
                       vectorizer_model = vectorizer_model).fit(news_list, embeddings)

Batches: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████| 498/498 [02:01<00:00,  4.09it/s]
2022-10-31 23:53:15,627 - BERTopic - Reduced dimensionality
2022-10-31 23:53:16,775 - BERTopic - Clustered reduced embeddings
2022-10-31 23:53:38,714 - BERTopic - Reduced number of topics from 23 to 23


In [68]:
topic_model.get_topic_info()

Topic  Count                                         Name
0      -1   9030        -1_κλιματική_αλλαγή_κλιματικής_ελλάδα
1       0    974  0_κλιματική_αλλαγή_περιβάλλοντος_κλιματικής
2       1    844   1_καύσωνα_θερμοκρασίες_βαθμούς_θερμοκρασία
3       2    640                2_συριζα_κυβέρνηση_2022_κρίση
4       3    613        3_ενέργειας_αερίου_φυσικού_ενεργειακή
5       4    588        4_κλιματική_αλλαγή_κλιματικής_πλανήτη
6       5    410                 5_χώρες_cop26_κλίμα_συμφωνία
7       6    355        6_τροφίμων_αγρότες_αγροτικής_παραγωγή
8       7    328          7_υγείας_ασθενειών_αλλαγή_ασθένειες
9       8    286               8_νατο_τουρκία_ελλάδα_τουρκίας
10      9    253        9_πυρκαγιά_πυρκαγιές_φωτιά_προστασίας
11     10    202          10_εκπομπών_νόμος_κτίρια_κλιματικός
12     11    156     11_διαδηλωτές_κλιματική_ακτιβιστές_cop26
13     12    144                12_νατο_ουκρανία_ρωσία_ρωσίας
14     13    138           13_debate_παύλος_ερώτηση_ερωτήσεις
15     14    138             14_αρκτική_πάγου_λιώσιμο_περιοχή
16     15    137                     15_κίνα_κίνας_ταϊβάν_ηπα
17     16    125                   16_κρίση_2022_πανδημία_νέα
18     17    124    17_protothema_τελευταίες_gr_ειδήσειςδείτε
19     18    111        18_φαινόμενα_λέκκας_πλημμυρικά_χρόνια
20     19    109      19_πρίγκιπας_κάρολος_βασίλισσα_ελισάβετ
21     20    104           20_protothema_gr_τελευταίες_nestlé
22     21    104         21_πακιστάν_πλημμύρες_παιδιά_βοήθεια

In [69]:
news_wrap = (df['summary'].str[:800].str.wrap(50)
             .apply(lambda x: x.replace('\n', '<br>')).to_list())

umap = UMAP(n_neighbors=10, n_components=2, min_dist=0.0,
            metric='cosine', random_state = 1)

reduced_embeddings = umap.fit_transform(embeddings)

fig = topic_model.visualize_documents(news_wrap, topics = list(range(50)),
                                      reduced_embeddings = reduced_embeddings, sample = 0.1)
fig.show()